In [87]:
import pandas as pd
import numpy as np
import seaborn as sns
import warnings
import matplotlib.pyplot as plt
from sklearn.ensemble import GradientBoostingRegressor
from pandas.tseries.offsets import *
warnings.filterwarnings('ignore')
%matplotlib inline

In [88]:
# description of the feature:
# Traffic Volume through the Tollgates
# time           datatime        the time when a vehicle passes the tollgate
# tollgate_id    string          ID of the tollgate
# direction      string           0:entry, 1:exit
# vehicle_model  int             this number ranges from 0 to 7, which indicates the capacity of the vehicle(bigger the higher)
# has_etc        string          does the vehicle use ETC (Electronic Toll Collection) device? 0: No, 1: Yes
# vehicle_type   string          vehicle type: 0-passenger vehicle, 1-cargo vehicle
volume_df = pd.read_csv("volume(table 6)_training.csv")
volume_df.head()

time  tollgate_id  direction  vehicle_model  has_etc  \
0  2016-09-19 23:09:25            2          0              1        0   
1  2016-09-19 23:11:53            2          0              1        0   
2  2016-09-19 23:13:54            2          0              1        0   
3  2016-09-19 23:17:48            1          0              1        1   
4  2016-09-19 23:16:07            2          0              1        0   

   vehicle_type  
0           NaN  
1           NaN  
2           NaN  
3           NaN  
4           NaN

In [89]:
# 替换所有有标签含义的数字
volume_df['tollgate_id'] = volume_df['tollgate_id'].replace({1:"1S", 2:"2S", 3:"3S"})
volume_df['direction'] = volume_df['direction'].replace({0:"entry", 1:"exit"})
volume_df['has_etc'] = volume_df['has_etc'].replace({0:"No", 1:"Yes"})
volume_df['vehicle_type'] = volume_df['vehicle_type'].replace({0:"passenger", 1:"carge"})
volume_df['time'] = volume_df['time'].apply(lambda x: pd.Timestamp(x))
volume_df.head()

time tollgate_id direction  vehicle_model has_etc  \
0 2016-09-19 23:09:25          2S     entry              1      No   
1 2016-09-19 23:11:53          2S     entry              1      No   
2 2016-09-19 23:13:54          2S     entry              1      No   
3 2016-09-19 23:17:48          1S     entry              1     Yes   
4 2016-09-19 23:16:07          2S     entry              1      No   

  vehicle_type  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN

In [90]:
# 承载量：1-默认客车，2-默认货车，3-默认货车，4-默认客车
# 承载量大于等于5的为货运汽车，所有承载量为0的车都类型不明
volume_df = volume_df.sort_values(by="vehicle_model")
vehicle_model0 = volume_df[volume_df['vehicle_model'] == 0].fillna("No")
vehicle_model1 = volume_df[volume_df['vehicle_model'] == 1].fillna("passenger")
vehicle_model2 = volume_df[volume_df['vehicle_model'] == 2].fillna("carge")
vehicle_model3 = volume_df[volume_df['vehicle_model'] == 3].fillna("carge")
vehicle_model4 = volume_df[volume_df['vehicle_model'] == 4].fillna("passenger")
vehicle_model5 = volume_df[volume_df['vehicle_model'] >= 5].fillna("carge")
volume_df = pd.concat([vehicle_model0, vehicle_model1, vehicle_model2, vehicle_model3, vehicle_model4, vehicle_model5])
volume_df[volume_df.isnull()].count()

time             0
tollgate_id      0
direction        0
vehicle_model    0
has_etc          0
vehicle_type     0
dtype: int64

In [94]:
# 创建之和流量，20分钟跨度有关系的训练集
# volume_time_entry = pd.Series(data = 1, index=volume_df.loc[(volume_df['tollgate_id']=="1S") & (volume_df['direction']=="entry"), :]['time'])
# volume_time_entry = volume_time_entry.resample("20T").sum()
# volume_entry = pd.DataFrame(index=volume_time_entry.index)
# volume_entry['volume'] = np.log(volume_time_entry)

# volume_time_exit = pd.Series(data = 1, index=volume_df.loc[(volume_df['tollgate_id']=="1S") & (volume_df['direction']=="exit"), :]['time'])
# volume_time_exit = volume_time_exit.resample("20T").sum()
# volume_exit = pd.DataFrame(index=volume_time_exit.index)
# volume_exit['volume'] = np.log(volume_time_exit)
# volume_exit
volume_all_entry = volume_df.loc[(volume_df['tollgate_id']=='1S') & (volume_df['direction']=='entry'), ["time", "vehicle_model"]]
volume_all_entry['volume'] = 1
volume_all_entry['cargo_count'] = volume_df['vehicle_type'].apply(lambda x: 1 if x == "carge" else 0)
volume_all_entry['passenger_count'] = volume_df['vehicle_type'].apply(lambda x: 1 if x == "passenger" else 0)
volume_all_entry['no_count'] = volume_df['vehicle_type'].apply(lambda x: 1 if x == "No" else 0)
volume_all_entry["cargo_model"] = volume_all_entry["cargo_count"] * volume_all_entry["vehicle_model"]
volume_all_entry["passenger_model"] = volume_all_entry["passenger_count"] * volume_all_entry["vehicle_model"]
volume_all_entry.index = volume_all_entry["time"]
del volume_all_entry["time"]
volume_all_entry = volume_all_entry.resample("20T").sum()
volume_all_entry["cargo_model_avg"] = volume_all_entry["cargo_model"] / volume_all_entry["cargo_count"]
volume_all_entry["passenger_model_avg"] = volume_all_entry["passenger_model"] / volume_all_entry["passenger_count"]
volume_all_entry["vehicle_model_avg"] = volume_all_entry["vehicle_model"] / volume_all_entry["volume"]
volume_all_entry = volume_all_entry.fillna(0)

volume_all_exit = volume_df.loc[(volume_df['tollgate_id']=='1S') & (volume_df['direction']=='exit'), ["time", "vehicle_model"]]
volume_all_exit["volume"] = 1
volume_all_exit["cargo_count"] = volume_df['vehicle_type'].apply(lambda x: 1 if x == "carge" else 0)
volume_all_exit["passenger_count"] = volume_df['vehicle_type'].apply(lambda x: 1 if x == "passenger" else 0)
volume_all_exit["no_count"] = volume_df['vehicle_type'].apply(lambda x: 1 if x == "No" else 0)
volume_all_exit["cargo_model"] = volume_all_exit["cargo_count"] * volume_all_exit["vehicle_model"]
volume_all_exit["passenger_model"] = volume_all_exit["passenger_count"] * volume_all_exit["vehicle_model"]
volume_all_exit.index = volume_all_exit["time"]
del volume_all_exit["time"]
volume_all_exit = volume_all_exit.resample("20T").sum()
volume_all_exit["cargo_model_avg"] = volume_all_exit["cargo_model"] / volume_all_exit["cargo_count"]
volume_all_exit["passenger_model_avg"] = volume_all_exit["passenger_model"] / volume_all_exit["passenger_count"]
volume_all_exit["vehicle_model_avg"] = volume_all_exit["vehicle_model"] / volume_all_exit["volume"]
volume_all_exit = volume_all_exit.fillna(0)

volume_all_exit

vehicle_model  volume  cargo_count  passenger_count  \
time                                                                       
2016-09-19 00:00:00          181.0   140.0         31.0            109.0   
2016-09-19 00:20:00           97.0    56.0         16.0             40.0   
2016-09-19 00:40:00           46.0    31.0         11.0             20.0   
2016-09-19 01:00:00            5.0     4.0          2.0              2.0   
2016-09-19 01:20:00           25.0    14.0          6.0              8.0   
2016-09-19 01:40:00           10.0     7.0          3.0              4.0   
2016-09-19 02:00:00           16.0     7.0          5.0              2.0   
2016-09-19 02:20:00           15.0     7.0          5.0              2.0   
2016-09-19 02:40:00           15.0    10.0          4.0              6.0   
2016-09-19 03:00:00           14.0    10.0          6.0              4.0   
2016-09-19 03:20:00           29.0    14.0         13.0              1.0   
2016-09-19 03:40:00           30.0    20.0         13.0              7.0   
2016-09-19 04:00:00           18.0    18.0         10.0              8.0   
2016-09-19 04:20:00           29.0    17.0         10.0              7.0   
2016-09-19 04:40:00           34.0    23.0         15.0              8.0   
2016-09-19 05:00:00           38.0    28.0         12.0             16.0   
2016-09-19 05:20:00           36.0    24.0         17.0              7.0   
2016-09-19 05:40:00           56.0    34.0         18.0             16.0   
2016-09-19 06:00:00           64.0    39.0         21.0             18.0   
2016-09-19 06:20:00           80.0    57.0         22.0             35.0   
2016-09-19 06:40:00          116.0    72.0         33.0             39.0   
2016-09-19 07:00:00           97.0    70.0         19.0             51.0   
2016-09-19 07:20:00          109.0    83.0         21.0             62.0   
2016-09-19 07:40:00          143.0   118.0         19.0             99.0   
2016-09-19 08:00:00          144.0   123.0         17.0            106.0   
2016-09-19 08:20:00          148.0   119.0         14.0            105.0   
2016-09-19 08:40:00          149.0   116.0         20.0             96.0   
2016-09-19 09:00:00          133.0   120.0         21.0             99.0   
2016-09-19 09:20:00          179.0   151.0         32.0            119.0   
2016-09-19 09:40:00          171.0   131.0         37.0             94.0   
...                            ...     ...          ...              ...   
2016-10-17 14:00:00          102.0    87.0         24.0             63.0   
2016-10-17 14:20:00          111.0    93.0         23.0             70.0   
2016-10-17 14:40:00          139.0   109.0         29.0             80.0   
2016-10-17 15:00:00          129.0    99.0         20.0             79.0   
2016-10-17 15:20:00          125.0    92.0         21.0             71.0   
2016-10-17 15:40:00          108.0    89.0         21.0             68.0   
2016-10-17 16:00:00          125.0   101.0         15.0             86.0   
2016-10-17 16:20:00          130.0   108.0         19.0             89.0   
2016-10-17 16:40:00          132.0   104.0         23.0             81.0   
2016-10-17 17:00:00          136.0   112.0         17.0             95.0   
2016-10-17 17:20:00          155.0   126.0         14.0            112.0   
2016-10-17 17:40:00          162.0   130.0         11.0            119.0   
2016-10-17 18:00:00           61.0    52.0          8.0             44.0   
2016-10-17 18:20:00          102.0    84.0         14.0             70.0   
2016-10-17 18:40:00           58.0    49.0          7.0             42.0   
2016-10-17 19:00:00           46.0    39.0          5.0             34.0   
2016-10-17 19:20:00           51.0    46.0          8.0             38.0   
2016-10-17 19:40:00           41.0    33.0          4.0             29.0   
2016-10-17 20:00:00           40.0    33.0          7.0             26.0   
2016-10-17 20:20:00           41.0    33.0          5.0             2

In [ ]:
# 创建训练集，总的要求就是以前两个小时数据为训练集，用迭代式预测方法
# 例如8点-10点的数据预测10点20,8点-10点20预测10点40……，每一次预测使用的都是独立的（可能模型一样）的模型
# 现在开始构建训练集
# 第一个训练集特征是所有两个小时（以20分钟为一个单位）的数据，因变量是该两小时之后20分钟的流量
# 第二个训练集，特征是所有两个小时又20分钟（以20分钟为一个单位）的数据，因变量是该两个小时之后20分钟的流量
# 以此类推训练12个GBDT模型，其中entry 6个，exit 6个（没调参）
old_index = volume_all_entry.columns
new_index = []
for i in range(6):
    new_index += [item + "%d" % (i) for item in old_index]
new_index.append("y")
models_entry = []
for j in range(1):
    train_df = pd.DataFrame()
    for i in range(len(volume_all_entry) - 6 - j):
#         df_temp = volume_entry.iloc[i:i + 6, 0]
#         df_temp = df_temp.append(pd.Series(volume_entry.iloc[i + 6 + j, 0]))
#         df_temp.index = range(7)
#         train_df = train_df.append(df_temp, ignore_index=True)
        se_temp = pd.Series()
        for k in range(6):
            se_temp = se_temp.append(volume_all_entry.iloc[i + k, :])
        se_temp = se_temp.append(pd.Series(volume_all_entry.iloc[i + 6 + j]["volume"]))
        se_temp.index = new_index
        se_temp.name = str(volume_all_entry.iloc[i, :].index)
        print se_temp
        train_df = train_df.append(se_temp)
    train_X = train_df.iloc[:, :-1].fillna(0)
    train_y = train_df["y"].fillna(0)
    model = GradientBoostingRegressor()
    model.fit(train_X, train_y)
    models_entry.append(model)

models_exit = []
for j in range(1):
    train_df = pd.DataFrame()
    for i in range(len(volume_all_exit) - 6 - j):
#         df_temp = volume_exit.iloc[i:i + 6, 0]
#         df_temp = df_temp.append(pd.Series(volume_exit.iloc[i + 6 + j, 0]))
#         df_temp.index = range(7)
#         train_df = train_df.append(df_temp, ignore_index=True)
        se_temp = pd.Series()
        for k in range(6):
            se_temp = se_temp.append(volume_all_exit.iloc[i + k, :])
        se_temp = se_temp.append(pd.Series(volume_all_exit.iloc[i + 6 + j]["volume"]))
        se_temp.index = new_index
        se_temp.name = str(volume_all_exit.iloc[i, :].index)
        train_df = train_df.append(se_temp)
    train_X = train_df.iloc[:, :-1].fillna(0)
    train_y = train_df.iloc[:, -1].fillna(0)
    model = GradientBoostingRegressor()
    model.fit(train_X, train_y)
    models_exit.append(model)

vehicle_model0          22.000000
volume0                 13.000000
cargo_count0             3.000000
passenger_count0        10.000000
no_count0                0.000000
cargo_model0            12.000000
passenger_model0        10.000000
cargo_model_avg0         4.000000
passenger_model_avg0     1.000000
vehicle_model_avg0       1.692308
vehicle_model1           6.000000
volume1                  6.000000
cargo_count1             0.000000
passenger_count1         6.000000
no_count1                0.000000
cargo_model1             0.000000
passenger_model1         6.000000
cargo_model_avg1         0.000000
passenger_model_avg1     1.000000
vehicle_model_avg1       1.000000
vehicle_model2          17.000000
volume2                  9.000000
cargo_count2             2.000000
passenger_count2         7.000000
no_count2                0.000000
cargo_model2             7.000000
passenger_model2        10.000000
cargo_model_avg2         3.500000
passenger_model_avg2     1.428571
vehicle_model_

In [105]:
volume_test = pd.read_csv("../testing_phase1/volume(table 6)_test1.csv")
volume_test.head()

time  tollgate_id  direction  vehicle_model  has_etc  \
0  2016-10-18 07:59:04            2          0              1        1   
1  2016-10-18 07:59:31            2          0              1        1   
2  2016-10-18 07:59:50            2          0              1        1   
3  2016-10-18 07:32:33            3          0              1        1   
4  2016-10-18 07:32:46            3          0              1        1   

   vehicle_type  
0           NaN  
1           NaN  
2           NaN  
3           NaN  
4           NaN

In [106]:
# 替换所有有标签含义的数字
volume_test['tollgate_id'] = volume_test['tollgate_id'].replace({1:"1S", 2:"2S", 3:"3S"})
volume_test['direction'] = volume_test['direction'].replace({0:"entry", 1:"exit"})
volume_test['has_etc'] = volume_test['has_etc'].replace({0:"No", 1:"Yes"})
volume_test['vehicle_type'] = volume_test['vehicle_type'].replace({0:"passenger", 1:"carge"})
volume_test['time'] = volume_test['time'].apply(lambda x: pd.Timestamp(x))
volume_test.head()

time tollgate_id direction  vehicle_model has_etc  \
0 2016-10-18 07:59:04          2S     entry              1     Yes   
1 2016-10-18 07:59:31          2S     entry              1     Yes   
2 2016-10-18 07:59:50          2S     entry              1     Yes   
3 2016-10-18 07:32:33          3S     entry              1     Yes   
4 2016-10-18 07:32:46          3S     entry              1     Yes   

  vehicle_type  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN

In [107]:
# 承载量：1-默认客车，2-默认货车，3-默认货车，4-默认客车
# 承载量大于等于5的为货运汽车，所有承载量为0的车都类型不明
volume_test = volume_test.sort_values(by="vehicle_model")
vehicle_model0 = volume_test[volume_test['vehicle_model'] == 0].fillna("No")
vehicle_model1 = volume_test[volume_test['vehicle_model'] == 1].fillna("passenger")
vehicle_model2 = volume_test[volume_test['vehicle_model'] == 2].fillna("carge")
vehicle_model3 = volume_test[volume_test['vehicle_model'] == 3].fillna("carge")
vehicle_model4 = volume_test[volume_test['vehicle_model'] == 4].fillna("passenger")
vehicle_model5 = volume_test[volume_test['vehicle_model'] >= 5].fillna("carge")
volume_test = pd.concat([vehicle_model0, vehicle_model1, vehicle_model2, vehicle_model3, vehicle_model4, vehicle_model5])
volume_test[volume_test.isnull()].count()

time             0
tollgate_id      0
direction        0
vehicle_model    0
has_etc          0
vehicle_type     0
dtype: int64

In [108]:
# 创建之和流量，20分钟跨度有关系的预测集
# volume_time_entry_test = pd.Series(data = 1, 
#                                    index=volume_test.loc[(volume_test['tollgate_id']=="2S") & (volume_test['direction']=="entry"), :]['time'])
# volume_time_entry_test = volume_time_entry_test.resample("20T").sum()
# volume_entry_test = pd.DataFrame(index=volume_time_entry_test.index)
# volume_entry_test['volume'] = volume_time_entry_test
# volume_entry_test = volume_entry_test.dropna()

# volume_time_exit_test = pd.Series(data = 1, 
#                                   index=volume_test.loc[(volume_test['tollgate_id']=="2S") & (volume_test['direction']=="exit"), :]['time'])
# volume_time_exit_test = volume_time_exit_test.resample("20T").sum()
# volume_exit_test = pd.DataFrame(index=volume_time_exit_test.index)
# volume_exit_test['volume'] = volume_time_exit_test
# volume_exit_test = volume_exit_test.dropna()
volume_entry_test = volume_test.loc[(volume_test['tollgate_id']=="1S") & (volume_test["direction"]=="entry"), ["time", "vehicle_model"]]
volume_entry_test["volume"] = 1
volume_entry_test["cargo_count"] = volume_test["vehicle_type"].apply(lambda x: 1 if x == "cargo" else 0)
volume_entry_test["passenger_count"] = volume_test["vehicle_type"].apply(lambda x: 1 if x == "passenger" else 0)
volume_entry_test["no_count"] = volume_test["vehicle_type"].apply(lambda x: 1 if x == "No" else 0)
volume_entry_test["cargo_model"] = volume_entry_test["cargo_count"] * volume_entry_test["vehicle_model"]
volume_entry_test["passenger_model"] = volume_entry_test["passenger_count"] * volume_entry_test["vehicle_model"]
volume_entry_test.index = volume_entry_test["time"]
del volume_entry_test["time"]
volume_entry_test = volume_all_entry.resample("20T").sum()
volume_entry_test["cargo_model_avg"] = volume_entry_test["cargo_model"] / volume_entry_test["cargo_count"]
volume_entry_test["passenger_model_avg"] = volume_entry_test["passenger_model"] / volume_entry_test["passenger_count"]
volume_entry_test["vehicle_model_avg"] = volume_entry_test["vehicle_model"] / volume_entry_test["volume"]
volume_entry_test = volume_entry_test.fillna(0)

volume_exit_test = volume_test.loc[(volume_test['tollgate_id']=="1S") & (volume_test["direction"]=="entry"), ["time", "vehicle_model"]]
volume_exit_test["volume"] = 1
volume_exit_test["cargo_count"] = volume_test["vehicle_type"].apply(lambda x: 1 if x == "cargo" else 0)
volume_exit_test["passenger_count"] = volume_test["vehicle_type"].apply(lambda x: 1 if x == "passenger" else 0)
volume_exit_test["no_count"] = volume_test["vehicle_type"].apply(lambda x: 1 if x == "No" else 0)
volume_exit_test["cargo_model"] = volume_exit_test["cargo_count"] * volume_exit_test["vehicle_model"]
volume_exit_test["passenger_model"] = volume_exit_test["passenger_count"] * volume_exit_test["vehicle_model"]
volume_exit_test.index = volume_exit_test["time"]
del volume_exit_test["time"]
volume_exit_test = volume_exit_test.resample("20T").sum()
volume_exit_test["cargo_model_avg"] = volume_exit_test["cargo_model"] / volume_exit_test["cargo_count"]
volume_exit_test["passenger_model_avg"] = volume_exit_test["passenger_model"] / volume_exit_test["passenger_count"]
volume_exit_test["vehicle_model_avg"] = volume_exit_test["vehicle_model"] / volume_exit_test["volume"]
volume_exit_test = volume_exit_test.fillna(0)

In [109]:
volume_entry_test

vehicle_model  volume  cargo_count  passenger_count  \
time                                                                       
2016-09-19 00:00:00           22.0    13.0          3.0             10.0   
2016-09-19 00:20:00            6.0     6.0          0.0              6.0   
2016-09-19 00:40:00           17.0     9.0          2.0              7.0   
2016-09-19 01:00:00           22.0    10.0          3.0              7.0   
2016-09-19 01:20:00           20.0    14.0          3.0             10.0   
2016-09-19 01:40:00           14.0    10.0          1.0              9.0   
2016-09-19 02:00:00           19.0     7.0          3.0              4.0   
2016-09-19 02:20:00           23.0    10.0          7.0              3.0   
2016-09-19 02:40:00           20.0     6.0          5.0              1.0   
2016-09-19 03:00:00           19.0     9.0          4.0              5.0   
2016-09-19 03:20:00            6.0     4.0          1.0              3.0   
2016-09-19 03:40:00           18.0     9.0          4.0              5.0   
2016-09-19 04:00:00           18.0    10.0          4.0              6.0   
2016-09-19 04:20:00           21.0    13.0          4.0              9.0   
2016-09-19 04:40:00           20.0    12.0          4.0              8.0   
2016-09-19 05:00:00            4.0     2.0          2.0              0.0   
2016-09-19 05:20:00           10.0     8.0          2.0              6.0   
2016-09-19 05:40:00           14.0    13.0          1.0             12.0   
2016-09-19 06:00:00           10.0     8.0          1.0              7.0   
2016-09-19 06:20:00           14.0    13.0          1.0             12.0   
2016-09-19 06:40:00           39.0    32.0          3.0             29.0   
2016-09-19 07:00:00           47.0    39.0          4.0             35.0   
2016-09-19 07:20:00           32.0    31.0          1.0             30.0   
2016-09-19 07:40:00           47.0    43.0          3.0             40.0   
2016-09-19 08:00:00           51.0    46.0          4.0             42.0   
2016-09-19 08:20:00           67.0    56.0          6.0             50.0   
2016-09-19 08:40:00           35.0    41.0          2.0             30.0   
2016-09-19 09:00:00           56.0    50.0          6.0             44.0   
2016-09-19 09:20:00           59.0    49.0          7.0             42.0   
2016-09-19 09:40:00           46.0    44.0          2.0             42.0   
...                            ...     ...          ...              ...   
2016-10-17 14:00:00           49.0    41.0          6.0             35.0   
2016-10-17 14:20:00           55.0    47.0          2.0             45.0   
2016-10-17 14:40:00           70.0    52.0          6.0             46.0   
2016-10-17 15:00:00           51.0    46.0          2.0             44.0   
2016-10-17 15:20:00           50.0    47.0          3.0             44.0   
2016-10-17 15:40:00           37.0    35.0          2.0             33.0   
2016-10-17 16:00:00           69.0    63.0          3.0             60.0   
2016-10-17 16:20:00           62.0    56.0          3.0             53.0   
2016-10-17 16:40:00           44.0    42.0          1.0             41.0   
2016-10-17 17:00:00           45.0    43.0          2.0             41.0   
2016-10-17 17:20:00           39.0    34.0          2.0             32.0   
2016-10-17 17:40:00           26.0    25.0          1.0             24.0   
2016-10-17 18:00:00           24.0    22.0          2.0             20.0   
2016-10-17 18:20:00           26.0    24.0          1.0             23.0   
2016-10-17 18:40:00           15.0    14.0          1.0             13.0   
2016-10-17 19:00:00           28.0    26.0          2.0             24.0   
2016-10-17 19:20:00           15.0    15.0          0.0             15.0   
2016-10-17 19:40:00           16.0    16.0          0.0             16.0   
2016-10-17 20:00:00           11.0    11.0          0.0             11.0   
2016-10-17 20:20:00           19.0    17.0          2.0             1

In [114]:
# 转换预测集，将预测集训练成和预测集第一个模型的格式相同（entry方向）
# se_temp = pd.Series()
#         for k in range(6):
#             se_temp = se_temp.append(volume_all_entry.iloc[i + k, :])
#         se_temp = se_temp.append(pd.Series(volume_entry.iloc[i + 6 + j, 0]))
#         se_temp.index = new_index
#         se_temp.name = str(volume_entry.iloc[i, :].index)
#         train_df = train_df.append(se_temp)
test_entry_df = pd.DataFrame()
i = 0
while i < len(volume_entry_test) - 5:
#     df_temp = volume_entry_test.iloc[i:i + 6, 0].T
#     df_temp.index = range(6)
#     df_temp.name = volume_entry_test.index[i]
#     test_entry_df = test_entry_df.append(df_temp)
    se_temp = pd.Series()
    for k in range(6):
        se_temp = se_temp.append(volume_entry_test.iloc[i + k, :])
    se_temp.index = new_index[:-1]
    se_temp.name = volume_entry_test.index[i]
    test_entry_df = test_entry_df.append(se_temp)
    i = i + 6

predict_test_entry = pd.DataFrame()
for i in range(6):
    test_y = models_entry[i].predict(test_entry_df)
    predict_test_entry[i] = test_y
predict_test_entry

0           1          2          3          4          5
0     8.943952   10.795692  13.889421  15.775883  19.456906  19.881573
1    10.059445   12.674009  13.630082  12.549288  18.247452  21.155938
2    13.045941   14.011648  24.217503  29.212668  27.410039  30.532368
3    40.804474   45.408814  42.296246  40.568806  42.935512  42.455880
4    46.967083   45.590510  45.388459  45.480782  43.371761  44.742197
5    36.833993   37.207814  34.974916  36.837064  36.395174  35.887015
6    53.348900   50.756499  49.639424  47.582438  47.097479  45.361158
7    45.750596   45.240058  46.880816  44.711315  45.725399  44.874567
8    25.414466   26.585184  25.680466  23.746784  23.903188  22.923752
9    25.106788   27.134283  28.305288  28.756075  29.036104  26.549723
10   10.843070    9.662349   9.569189  12.067594  11.614265  10.478070
11    9.601778   10.997078  11.494866  11.717943  13.330150  11.848862
12    7.218548    7.664791   6.103354   5.982663   6.768556   6.793899
13    8.435712    7.935838  12.064334  13.382140  19.568048  19.723225
14   11.693304   15.555249  23.235109  29.635901  31.629036  39.836842
15   36.841512   36.540703  35.288248  35.202418  37.006196  35.956628
16   52.722875   56.764875  53.386049  49.724977  49.303880  45.669592
17   49.407763   48.777751  49.204812  48.072890  45.872072  44.825393
18   80.428484   77.530375  77.830530  72.027473  70.139294  70.932249
19   73.308901   74.963795  68.683033  65.710731  64.775833  59.033505
20   40.121510   35.064202  35.963855  32.779310  30.683039  30.302960
21   21.573331   20.231288  18.866087  17.061913  15.135944  13.352322
22   36.350288   39.852257  37.767688  38.271293  42.141198  41.566786
23   10.622737   12.787905  15.037489  21.033931  25.391619  28.485184
24    8.361753   10.561351  13.408087  13.819670  13.952179  17.277551
25   10.933082    9.590315  11.871969  13.185804  14.345462  17.236189
26   30.614330   34.400914  52.880189  51.536155  60.596971  49.677169
27   98.536633  100.748246  95.775687  89.286967  66.836180  79.571163
28   52.777248   52.504899  50.780050  47.021076  44.854435  42.546227
29   33.681529   35.991254  35.141069  39.823399  35.603716  37.136195
..         ...         ...        ...        ...        ...        ...
318  39.871089   35.412495  35.960911  30.682951  31.005634  31.854190
319  51.755539   49.246942  46.212673  46.350502  42.220965  40.914175
320  38.926806   35.312284  36.050620  35.326283  31.663146  32.305008
321  22.675651   21.778466  21.587463  20.943904  20.766755  17.536315
322  19.782236   17.383079  15.719085  15.431426  15.773154  12.769618
323   8.134798    9.746336   9.256122   8.327503   9.459779   9.168294
324   7.786878    9.885027  11.964721  15.634222  21.125075  24.798914
325   9.037240   10.167650  14.510327   8.217297   8.595572  11.857248
326   9.967638   13.596494  17.176972  26.602738  30.714964  31.738211
327  46.156079   51.891988  52.395848  50.688370  45.080476  46.952567
328  45.708918   48.102481  47.084267  43.810135  41.090680  41.941418
329  28.909707   26.596774  27.583485  25.851794  27.097858  28.747686
330  47.577125   46.546009  46.575281  45.667196  45.038813  43.696069
331  71.500208   71.897374  69.891775  68.831335  62.118360  54.283034
332  44.868402   38.963677  39.082465  34.971457  36.179866  35.901055
333  35.823556   34.021211  31.352647  29.232626  28.958664  28.244205
334  16.739964   12.658870  11.364740  11.499251  11.139039  11.447781
335   8.420113   10.297737   9.324781   8.573390   8.547517   8.459419
336   8.633584   11.367196  13.725546  16.008990  19.961347  17.833508
337   7.697787    7.759970   7.287428   8.200534   7.766822  10.715292
338  10.043378   14.004784  15.902009  29.410096  27.686217  35.044035
339  52.514374   50.958287  54.304326  52.283605  52.306829  48.387189
340  44.697348   45.968618  43.121260  43.349095  42.531900  40.011933
341  34.242281   32.996081  33.958259  34.426578  33.542225  35.245391
342  50.043048   55.226414  50.771885

In [116]:
# 转换预测集，将预测集训练成和预测集第一个模型的格式相同（exit方向）
test_exit_df = pd.DataFrame()
i = 0
while i < len(volume_exit_test) - 5:
#     df_temp = volume_exit_test.iloc[i:i + 6, 0].T
#     df_temp.index = range(6)
#     df_temp.name = volume_exit_test.index[i]
#     test_exit_df = test_exit_df.append(df_temp)
    se_temp = pd.Series()
    for k in range(6):
        se_temp = se_temp.append(volume_exit_test.iloc[i + k, :])
    se_temp.index = new_index[:-1]
    se_temp.name = volume_exit_test.index[i]
    test_exit_df = test_exit_df.append(se_temp)
    i = i + 6

predict_test_exit = pd.DataFrame()
for i in range(6):
    test_y = models_exit[i].predict(test_exit_df)
    predict_test_exit[i + 6] = test_y
predict_test_exit

6          7          8          9          10         11
0   55.547774  22.185411  31.948173  22.779954  52.815177  53.494851
1   31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
2   31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
3   31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
4   42.635392   0.541804  34.684789  21.892374  19.689519  26.679867
5   43.049443  30.909601  21.543476  51.614100  40.058943  17.318972
6   31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
7   31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
8   31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
9   31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
10  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
11  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
12  39.133447  21.309337  26.386840  23.904966  33.247537  29.363962
13  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
14  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
15  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
16  47.363813   0.614531  22.940435  27.502392  23.691510  26.679867
17  42.074377  30.909601  35.559854  56.021843  40.656228  23.120953
18  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
19  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
20  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
21  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
22  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
23  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
24  42.213141  19.967713  26.230803  29.865407  49.575106  28.396538
25  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
26  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
27  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
28  43.471757   0.695983  22.577301  18.695257  18.650478  37.072857
29  50.660801  30.909601  20.348456  56.146507  46.354798  25.151462
..        ...        ...        ...        ...        ...        ...
47  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
48  52.288077  34.880535  25.521520  50.379826  54.040525  45.380099
49  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
50  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
51  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
52  53.566775  -1.669370  22.940435  19.357608  18.650478  37.072857
53  43.049443  30.909601  21.543476  50.746884  40.940921  17.613728
54  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
55  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
56  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
57  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
58  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
59  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
60  41.907295   6.274087  34.006319  41.135300  40.310248  31.490948
61  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
62  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
63  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
64  54.083344   0.803285  29.031734  17.817981  15.093837  28.500011
65  48.698788  26.716202  21.543476  52.166681  42.130772  17.042635
66  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
67  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
68  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
69  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
70  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
71  31.494431   4.592343   8.127071  11.591925   8.133314  14.456936
72  56.616508  42.627886  30.093777  49.903383  50.793665  42.897478
73  31.49

In [72]:
def transform_predict(predict_original, direction, tollgate_id):
    result = pd.DataFrame()
    for i in range(len(predict_original)):
        time_basic = predict_original.index[i]
        for j in range(6, 12, 1):
            time_window = "[" + str(time_basic + DateOffset(minutes=j * 20)) + "," + str(time_basic + DateOffset(minutes=(j + 1) * 20)) + ")"
            series = pd.Series({"tollage_id": tollgate_id, 
                                "time_window": time_window, 
                                "direction": direction, 
                                "volume": predict_original.iloc[i, j]})
            series.name = i + j - 6
            result = result.append(series)
    return result

print transform_predict(predict_test_entry, "entry", "1S")

   direction                                time_window tollage_id     volume
0      entry  [2016-10-18 08:00:00,2016-10-18 08:20:00)         1S  45.806886
1      entry  [2016-10-18 08:20:00,2016-10-18 08:40:00)         1S  52.958557
2      entry  [2016-10-18 08:40:00,2016-10-18 09:00:00)         1S  57.946432
3      entry  [2016-10-18 09:00:00,2016-10-18 09:20:00)         1S  61.429576
4      entry  [2016-10-18 09:20:00,2016-10-18 09:40:00)         1S  65.694853
5      entry  [2016-10-18 09:40:00,2016-10-18 10:00:00)         1S  77.994429
1      entry  [2016-10-18 17:00:00,2016-10-18 17:20:00)         1S  49.460976
2      entry  [2016-10-18 17:20:00,2016-10-18 17:40:00)         1S  48.004843
3      entry  [2016-10-18 17:40:00,2016-10-18 18:00:00)         1S  47.042836
4      entry  [2016-10-18 18:00:00,2016-10-18 18:20:00)         1S  43.703965
5      entry  [2016-10-18 18:20:00,2016-10-18 18:40:00)         1S  43.210875
6      entry  [2016-10-18 18:40:00,2016-10-18 19:00:00)         